In [1]:
import keras
from keras.layers import Activation, Dense, Dropout, Conv2D, \
                         Flatten, MaxPooling2D
from keras.models import Sequential
import librosa
import librosa.display
import numpy as np
import pandas as pd
import random

import warnings
warnings.filterwarnings('ignore')

In [4]:
import json
with open('original.json', "r") as f:
    data = json.load(f)

#X = np.array(data["spect"])
#y = np.array(data["label"])
D = np.array(data)


In [23]:
file_name = 'F01/Session1/wav_arrayMic/0001.wav'
y, sr = librosa.load(file_name, duration=5.0)
ps = librosa.feature.melspectrogram(y=y, sr=sr)
ps.shape

(128, 216)

In [24]:
type(ps)

numpy.ndarray

In [25]:
import numpy as np

arr = np.random.randint(0, 10, (7, 4))

def padding(array, xx, yy):
    """
    :param array: numpy array
    :param xx: desired height
    :param yy: desirex width
    :return: padded array
    """

    h = array.shape[0]
    w = array.shape[1]

    a = (xx - h) // 2
    aa = xx - a - h

    b = (yy - w) // 2
    bb = yy - b - w

    return np.pad(array, pad_width=((a, aa), (b, bb)), mode='constant')

In [33]:
x=data['spect']

In [36]:
type(x[0])

list

In [45]:
sample=len(x)
row=len(x[0])
col=len(x[0][0])
sample,row,col

(9238, 128, 362)

In [46]:
y=data["label"]

In [50]:
a=x[0]
type(a)

list

In [51]:
a=np.array(a)
type(a)

numpy.ndarray

In [52]:
a.shape

(128, 362)

In [53]:
a=padding(a,128,400)


In [54]:
type(a)

numpy.ndarray

In [55]:
a.shape

(128, 400)

In [56]:
D=[]
#for f, b in zip(foo, bar):
#    print(f, b)
for ps,label in zip(x,y):
    D.append( (np.array(padding(np.array(ps),128,400)), label) )

In [58]:
len(D)

9238

In [59]:
dataset = D
random.shuffle(dataset)

train = dataset[:8000]
dataset = dataset[8000:]
validate = dataset[:1000]
test = dataset[1000:]

X_train, y_train = zip(*train)
X_validate, y_validate = zip(*validate)
X_test, y_test = zip(*test)

# Reshape for CNN input
X_train = np.array([x.reshape( (128, 400, 1) ) for x in X_train])
X_validate = np.array([x.reshape( (128, 400, 1) ) for x in X_validate])
X_test = np.array([x.reshape( (128, 400, 1) ) for x in X_test])

In [60]:
from tensorflow.keras.utils import to_categorical
from sklearn.preprocessing import LabelEncoder
labelencoder=LabelEncoder()
#y=to_categorical(labelencoder.fit_transform(y))
#y
y_train = np.array(to_categorical(labelencoder.fit_transform(y_train)))
y_validate = np.array(to_categorical(labelencoder.fit_transform(y_validate)))
y_test = np.array(to_categorical(labelencoder.fit_transform(y_test)))

In [61]:
X_train.shape, X_validate.shape, X_test.shape, y_train.shape, y_validate.shape, y_test.shape

((8000, 128, 400, 1),
 (1000, 128, 400, 1),
 (238, 128, 400, 1),
 (8000, 2),
 (1000, 2),
 (238, 2))

In [62]:
reconstructed_model = keras.models.load_model("original_model")

In [64]:
score = reconstructed_model.evaluate(x=X_test,y=y_test)
print('Test loss:', score[0])
print('Test accuracy:', score[1])

8/8 [==============================] - 40s 403ms/step - loss: 0.2171 - accuracy: 0.9202
Test loss: 0.21707461774349213
Test accuracy: 0.9201680421829224


In [65]:
predict = reconstructed_model.predict_classes(X_test)
prediction_class = labelencoder.inverse_transform(predict)
#real_class = labelencoder.inverse_transform(y_test)
#prediction_class
x, y = zip(*test)
y
match = 0
print('  Real       Prediction       Match')
for i in range(0,X_test.shape[0]):
    if(y[i]==prediction_class[i]):
        match+=1
    print(y[i] + '       ' + prediction_class[i] + '       ' + str(y[i]==prediction_class[i]))
print('Matched = ', match)
print('Not Matched = ',(X_test.shape[0] - match))

  Real       Prediction       Match
Typical       Typical       True
Typical       Typical       True
Atypical       Atypical       True
Typical       Typical       True
Typical       Atypical       False
Typical       Typical       True
Typical       Typical       True
Typical       Typical       True
Typical       Typical       True
Atypical       Typical       False
Atypical       Typical       False
Typical       Typical       True
Typical       Typical       True
Atypical       Atypical       True
Atypical       Atypical       True
Typical       Typical       True
Typical       Typical       True
Typical       Typical       True
Typical       Typical       True
Typical       Typical       True
Typical       Typical       True
Typical       Typical       True
Typical       Typical       True
Typical       Typical       True
Typical       Typical       True
Typical       Typical       True
Atypical       Atypical       True
Typical       Typical       True
Typical       Typical     

In [67]:
x=data['spect']
y=data['label']

In [70]:
type(x[0])

list

In [71]:
a=x[0]
type(a)

list

In [72]:
b=y[0]
b

'Atypical'

In [73]:
d=[] 
d.append( (np.array(padding(np.array(a),128,400)), b) )
d

[(array([[0., 0., 0., ..., 0., 0., 0.],
         [0., 0., 0., ..., 0., 0., 0.],
         [0., 0., 0., ..., 0., 0., 0.],
         ...,
         [0., 0., 0., ..., 0., 0., 0.],
         [0., 0., 0., ..., 0., 0., 0.],
         [0., 0., 0., ..., 0., 0., 0.]]),
  'Atypical')]

In [80]:
d[0]

(array([[0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        ...,
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.]]),
 'Atypical')

In [78]:
a=x[1]
b=y[1]
d.append( (padding(np.array(a),128,400), b) )

In [81]:
d[1]

(array([[0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        ...,
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.]]),
 'Atypical')

In [84]:
a=x[1]
a

[[0.007594119757413864,
  0.0020112735219299793,
  0.0005369793507270515,
  0.0006083613261580467,
  0.0003534704155754298,
  0.0002339949569432065,
  0.00027882197173312306,
  0.0004671118804253638,
  0.0008009810699149966,
  0.00026701216120272875,
  0.0002794950851239264,
  0.00041578675154596567,
  0.0006226326222531497,
  0.0006256786873564124,
  0.00020489635062403977,
  0.00013545429101213813,
  0.0003141823399346322,
  0.0011603499297052622,
  0.0006269278237596154,
  0.00019423862977419049,
  0.0002639091107994318,
  0.0005037678056396544,
  0.0006970022805035114,
  0.0002226525393780321,
  0.00029429138521663845,
  0.00027355883503332734,
  0.00020048837177455425,
  0.00019938463810831308,
  0.0001847184612415731,
  0.00013524509267881513,
  5.8960780734196305e-05,
  0.0002179222647100687,
  0.0007510111317969859,
  0.00035170544288121164,
  0.00012671196600422263,
  0.00032628182088956237,
  0.000325784960296005,
  0.0003894344554282725,
  0.0004328837094362825,
  0.00014373

In [85]:
a=padding(np.array(a),128,400)
a

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

In [86]:
a=a.tolist()
a

[[0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.007594119757413864,
  0.0020112735219299793,
  0.0005369793507270515,
  0.0006083613261580467,
  0.0003534704155754298,
  0.0002339949569432065,
  0.00027882197173312306,
  0.0004671118804253638,
  0.0008009810699149966,
  0.00026701216120272875,
  0.0002794950851239264,
  0.00041578675154596567,
  0.0006226326222531497,
  0.0006256786873564124,
  0.00020489635062403977,
  0.00013545429101213813,
  0.0003141823399346322,
  0.0011603499297052622,
  0.0006269278237596154,
  0.00019423862977419049,
  0.0002639091107994318,
  0.0005037678056396544,
  0.00069700228050

In [87]:
a=x[1]
a

[[0.007594119757413864,
  0.0020112735219299793,
  0.0005369793507270515,
  0.0006083613261580467,
  0.0003534704155754298,
  0.0002339949569432065,
  0.00027882197173312306,
  0.0004671118804253638,
  0.0008009810699149966,
  0.00026701216120272875,
  0.0002794950851239264,
  0.00041578675154596567,
  0.0006226326222531497,
  0.0006256786873564124,
  0.00020489635062403977,
  0.00013545429101213813,
  0.0003141823399346322,
  0.0011603499297052622,
  0.0006269278237596154,
  0.00019423862977419049,
  0.0002639091107994318,
  0.0005037678056396544,
  0.0006970022805035114,
  0.0002226525393780321,
  0.00029429138521663845,
  0.00027355883503332734,
  0.00020048837177455425,
  0.00019938463810831308,
  0.0001847184612415731,
  0.00013524509267881513,
  5.8960780734196305e-05,
  0.0002179222647100687,
  0.0007510111317969859,
  0.00035170544288121164,
  0.00012671196600422263,
  0.00032628182088956237,
  0.000325784960296005,
  0.0003894344554282725,
  0.0004328837094362825,
  0.00014373

In [89]:
a=np.array(padding(np.array(a),128,400))
a

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

In [90]:
a=a.tolist()
a

[[0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.007594119757413864,
  0.0020112735219299793,
  0.0005369793507270515,
  0.0006083613261580467,
  0.0003534704155754298,
  0.0002339949569432065,
  0.00027882197173312306,
  0.0004671118804253638,
  0.0008009810699149966,
  0.00026701216120272875,
  0.0002794950851239264,
  0.00041578675154596567,
  0.0006226326222531497,
  0.0006256786873564124,
  0.00020489635062403977,
  0.00013545429101213813,
  0.0003141823399346322,
  0.0011603499297052622,
  0.0006269278237596154,
  0.00019423862977419049,
  0.0002639091107994318,
  0.0005037678056396544,
  0.00069700228050